# Step 2: Cleaning

In [4]:
SELECT TOP 10 * FROM stock_data;

(10 rows affected)

Total execution time: 00:00:00.009

company date close volume open high low AAPL 2013-07-18 15.42 218632537 15.48 15.53 15.38 AAPL 2013-07-19 15.18 268548901 15.47 15.5 15.16 AAPL 2013-07-22 15.23 207648981 15.34 15.35 15.2 AAPL 2013-07-23 14.96 354477618 15.21 15.25 14.95 AAPL 2013-07-24 15.73 591624923 15.68 15.88 15.55 AAPL 2013-07-25 15.66 229432412 15.74 15.76 15.56 AAPL 2013-07-26 15.75 200082264 15.55 15.75 15.51 AAPL 2013-07-29 15.99 248025441 15.74 16.07 15.72 AAPL 2013-07-30 16.19 308960556 16.07 16.33 16.04 AAPL 2013-07-31 16.16 322499391 16.25 16.33 16.05

## A. Check for NULL values

In [5]:
-- Count the number of NULL values in each column
SELECT 
    SUM(CASE WHEN company IS NULL THEN 1 ELSE 0 END) AS company_nulls,
    SUM(CASE WHEN [date] IS NULL THEN 1 ELSE 0 END) AS date_nulls,
    SUM(CASE WHEN [close] IS NULL THEN 1 ELSE 0 END) AS close_nulls,
    SUM(CASE WHEN volume IS NULL THEN 1 ELSE 0 END) AS volume_nulls,
    SUM(CASE WHEN [open] IS NULL THEN 1 ELSE 0 END) AS open_nulls,
    SUM(CASE WHEN high IS NULL THEN 1 ELSE 0 END) AS high_nulls,
    SUM(CASE WHEN low IS NULL THEN 1 ELSE 0 END) AS low_nulls
FROM stock_data;

-- No NULL values! 

(1 row affected)

Total execution time: 00:00:00.023

company_nulls date_nulls close_nulls volume_nulls open_nulls high_nulls low_nulls 0 0 0 0 0 0 0

## B. Check for data type consistency

In [6]:
-- Get the data type for each column
SELECT COLUMN_NAME, DATA_TYPE
FROM INFORMATION_SCHEMA.COLUMNS
WHERE TABLE_NAME = 'stock_data';

(7 rows affected)

Total execution time: 00:00:00.049

COLUMN_NAME DATA_TYPE company varchar date date close float volume int open float high float low float

In [7]:
-- Ensure all values in date column are in DATE format
SELECT *
FROM stock_data
WHERE TRY_CAST(date AS DATE) IS NULL;

-- Looks good! 

(0 rows affected)

Total execution time: 00:00:00.053

company date close volume open high low

In [9]:
-- Ensure all values in close, open, high, low columsn are in numeric format
SELECT *
FROM stock_data
WHERE TRY_CAST([close] AS FLOAT) IS NULL
   OR TRY_CAST(volume AS FLOAT) IS NULL
   OR TRY_CAST([open] AS FLOAT) IS NULL
   OR TRY_CAST(high AS FLOAT) IS NULL
   OR TRY_CAST(low AS FLOAT) IS NULL;

-- Looks good! 

(0 rows affected)

Total execution time: 00:00:00.074

company date close volume open high low

## C. Check for outliers

### i. In the close column

In [13]:
-- Return all rows with outliers

WITH Percentiles AS (
    SELECT
        PERCENTILE_CONT(0.25) WITHIN GROUP (ORDER BY [close]) OVER () AS Q1,
        PERCENTILE_CONT(0.75) WITHIN GROUP (ORDER BY [close]) OVER () AS Q3
    FROM stock_data
),
Bounds AS (
    SELECT 
        (Q3 - Q1) AS IQR,
        (Q1 - 1.5 * (Q3 - Q1)) AS Lower_Bound,
        (Q3 + 1.5 * (Q3 - Q1)) AS Upper_Bound
    FROM Percentiles
)
SELECT *
FROM stock_data, Bounds
WHERE [close] < Lower_Bound OR [close] > Upper_Bound;

(47854320 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:15:03.627

company date close volume open high low IQR Lower_Bound Upper_Bound META 2020-08-25 280.82 42127240 272.41 283.09 270.26 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-08-26 303.91 69015150 284 304.67 284 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-08-27 293.22 30301310 300.16 301.23 292.02 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-08-28 293.66 17172420 295 297.23 290.98 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-08-31 293.2 17345130 293.95 296.88 291.55 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-09-01 295.44 17320870 294.71 301.49 292.71 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-09-02 302.5 24341370 298.88 303.6 293.05 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-09-03 291.12 32294090 295.99 297.6 283.63 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-09-04 282.73 30333670 287.25 289 271.14 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-10-23 284.79 17535160 278.8 285.24 276.82 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-10-27 283.29 16287250 278.76 284.51 276.31 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-10-29 280.83 32368120 276.55 283.6 273.78 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-11-04 287.38 35364420 281 288.94 278.62 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-11-05 294.68 23823630 291.9 297.38 288.95 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-11-06 293.41 13890970 293.95 294.6 288.06 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-12-01 286.55 20777910 279.16 289.3 278.96 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-12-02 287.52 17361620 285.36 291.78 280.83 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-12-03 281.85 12921690 286.25 286.65 281.07 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-12-07 285.58 13007670 279.19 288.49 278.2 97.66749999999999 -109.93374999999997 280.7362499999999 META 2020-12-08 283.4 10747650 286.01 286.43 281.55 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-01-26 282.05 19373640 278.14 285.39 277.81 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-03-17 284.01 21315040 275.71 286.23 275.41 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-03-19 290.11 38930540 281.22 292.8 281.2 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-03-22 293.54 28273070 290.45 299.71 286.75 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-03-23 290.63 23000930 293.15 298 289.81 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-03-24 282.14 18675050 291 291.72 281.16 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-03-26 283.02 17629190 278.3 284.5 277.77 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-03-29 290.82 21718830 285.77 293.18 284.7 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-03-30 288 17474540 289.83 292.47 286.7 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-03-31 294.53 19498160 289.99 296.5 288.61 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-04-01 298.66 17615980 298.4 302.4 296.6 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-04-05 308.91 28237010 300.89 310.77 300.68 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-04-06 306.26 17335250 308.84 311.35 305.25 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-04-07 313.09 22855240 306.34 314.25 305.5 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-04-08 313.02 20894150 314.85 315.88 310.05 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-04-09 312.46 15988570 311.4 314.74 310.33 97.66749999999999 -109.93374999999997 280.7362499999999 META 2021-04-12 311.54 10881940 311.05 312.15 307.93 97

In [14]:
-- Count the number of outliers

WITH Percentiles AS (
    SELECT
        PERCENTILE_CONT(0.25) WITHIN GROUP (ORDER BY [close]) OVER () AS Q1,
        PERCENTILE_CONT(0.75) WITHIN GROUP (ORDER BY [close]) OVER () AS Q3
    FROM stock_data
),
Bounds AS (
    SELECT 
        (Q3 - Q1) AS IQR,
        (Q1 - 1.5 * (Q3 - Q1)) AS Lower_Bound,
        (Q3 + 1.5 * (Q3 - Q1)) AS Upper_Bound
    FROM Percentiles
)
SELECT COUNT(*)
FROM stock_data, Bounds
WHERE [close] < Lower_Bound OR [close] > Upper_Bound;

(1 row affected)

Total execution time: 00:00:00.439

(No column name) 47854320